In [0]:
# %skip
# spark.conf.set("spark.sql.execution.arrow.maxRecordsPerBatch",10)
%pip install chonkie[all] llama_index typing transformers unstructured[all-docs]

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 981.5/981.5 kB 24.3 MB/s eta 0:00:00
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
  Using cached httpcore-1.0.9-py3-none-any.whl.metadata (21 kB)
  Using cached h11-0.16.0-py3-none-any.whl.metadata (8.3 kB)
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.4/17.4 MB 109.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.0/5.0 MB 121.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 608.4/608.4 kB 27.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 538.2/538.2 kB 21.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.6/6.6 MB 93.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.4/1.4 MB 47.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.4/2.4 MB 70.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [0]:
dbutils.library.restartPython()

In [0]:
%sql
USE CATALOG dev_appian_poc;
USE SCHEMA 02_gold;

In [0]:
df = spark.table("document_text_contents")
# bronze_df = spark.table("dev_appian_poc.`00_bronze`.appian_raw_documents_ingest")

In [0]:
test_df = df.limit(1)
test_df.display()

path text full_text dbfs:/Volumes/dev_appian_poc/00_bronze/landing_zone/file_uploads/COST-Annual-Report-2025.pdf List(null, Costco WHOLESALE 2025 ANNUAL REPORT FISCAL YEAR ENDED AUGUST 31, 2025, null, December 4, 2025, Dear Costco Shareholders,, Our commitment to provide our members with an assortment of great quality merchandise and services that offer excitement, discovery and meet their everyday needs at the lowest possible price is at the core of what makes Costco successful. Our employees are the heartbeat of our company, as they bring this to life for our members every day, and their experience and dedication is the key to sustaining our culture and our continued success., We are committed to providing our employees with industry-leading pay and benefits around the world. In 2025, we made additional investments in employee wages, bringing our average hourly wage in the U.S. to approximately $32 for hourly employees. When healthcare, retirement, and other benefits are included, total compensation averaged approximately $46 per hour for those hourly employees., Net sales for fiscal year 2025 totaled $269.9 billion, an increase of 8%. Net income was $8.1 billion, or $18.21 per diluted share, an increase of 10%. Revenue from membership fees increased by 10% to $5.3 billion, and our membership base expanded to over 145 million cardholders, with a 90% renewal rate. Costco's expansion in fiscal 2025 included 24 net new locations: 15 in the U.S., two each in Canada, Mexico, and Japan, and one each in Spain, Sweden, and South Korea; resulting in 914 locations., Our global buying teams are doing a remarkable job navigating a changing economic and geopolitical environment, while continuing to deliver increased value for our members. They are achieving this by working closely with our suppliers, collaborating globally to identify new, great-value items, expanding in-country production and optimizing our supply chain for efficiency. We are leveraging the benefits of our limited sku count model to dynamically adjust the items we sell, to focus on those which are the most productive, allowing us to lower costs and pass on the savings., We are also focused on longer-term decisions that will ensure we are able to increase member values relative to the market in the future, including investments in our Kirkland Signature private label and Digital capabilities., Kirkland Signature™ is an important component of our value proposition, typically offering 15-20% savings compared to the national brand equivalent item, with equal or better quality. We celebrated the 30th anniversary of our Kirkland Signature trademark this year, and it continues to enjoy strong growth, now representing approximately $90B of annual revenue globally. In fiscal year 2025, to support future growth we expanded our manufacturing production capabilities in meat and coffee and introduced a wide range of new Kirkland Signature items, including food-storage bags, grass-fed meat sticks, and ready-to-drink cocktails., Our digital growth globally outpaced overall sales growth in 2025, and members who engage with us through our digital channels are also more loyal. We operate eight e-commerce platforms around the world and digitally enabled sales, those initiated through a digital device and fulfilled through a warehouse or distribution center and Costco Travel, represented approximately $27B of net sales last year.
E-commerce channels provide us with the opportunity to offer an expanded selection in various categories, including precious metals, ticket programs, appliances, home furnishings, consumer electronics, lawn and garden products, health and beauty aids, apparel, and groceries. As we continue our investments in technology, we are building a multi-year roadmap to create a more seamless digital experience for members. In 2025, we delivered numerous enhancements to the member experience, both in the warehouse and online, including improvements to the Costco app, increas

In [0]:
from chonkie import RecursiveChunker
import pandas as pd
from typing import Iterator
from pyspark.sql.functions import pandas_udf, explode

@pandas_udf("array<string>")
def read_as_chunk(batch_iter : Iterator[pd.Series]) -> Iterator[pd.Series]:
    chunker = RecursiveChunker()
    for batch in batch_iter:
        result_chunk = []
        for text in batch:
            if text and isinstance(text, str):
                chunks = chunker(text)
                chunk_text = [str(chunk) for chunk in chunks]
                result_chunk.append(chunk_text)
            else:
                result_chunk.append([])
        yield pd.Series(result_chunk)


In [0]:
df_chunks = test_df.withColumn("full_text", explode(read_as_chunk("full_text")))

In [0]:
df_chunks.display()

path text full_text dbfs:/Volumes/dev_appian_poc/00_bronze/landing_zone/file_uploads/COST-Annual-Report-2025.pdf List(null, Costco WHOLESALE 2025 ANNUAL REPORT FISCAL YEAR ENDED AUGUST 31, 2025, null, December 4, 2025, Dear Costco Shareholders,, Our commitment to provide our members with an assortment of great quality merchandise and services that offer excitement, discovery and meet their everyday needs at the lowest possible price is at the core of what makes Costco successful. Our employees are the heartbeat of our company, as they bring this to life for our members every day, and their experience and dedication is the key to sustaining our culture and our continued success., We are committed to providing our employees with industry-leading pay and benefits around the world. In 2025, we made additional investments in employee wages, bringing our average hourly wage in the U.S. to approximately $32 for hourly employees. When healthcare, retirement, and other benefits are included, total compensation averaged approximately $46 per hour for those hourly employees., Net sales for fiscal year 2025 totaled $269.9 billion, an increase of 8%. Net income was $8.1 billion, or $18.21 per diluted share, an increase of 10%. Revenue from membership fees increased by 10% to $5.3 billion, and our membership base expanded to over 145 million cardholders, with a 90% renewal rate. Costco's expansion in fiscal 2025 included 24 net new locations: 15 in the U.S., two each in Canada, Mexico, and Japan, and one each in Spain, Sweden, and South Korea; resulting in 914 locations., Our global buying teams are doing a remarkable job navigating a changing economic and geopolitical environment, while continuing to deliver increased value for our members. They are achieving this by working closely with our suppliers, collaborating globally to identify new, great-value items, expanding in-country production and optimizing our supply chain for efficiency. We are leveraging the benefits of our limited sku count model to dynamically adjust the items we sell, to focus on those which are the most productive, allowing us to lower costs and pass on the savings., We are also focused on longer-term decisions that will ensure we are able to increase member values relative to the market in the future, including investments in our Kirkland Signature private label and Digital capabilities., Kirkland Signature™ is an important component of our value proposition, typically offering 15-20% savings compared to the national brand equivalent item, with equal or better quality. We celebrated the 30th anniversary of our Kirkland Signature trademark this year, and it continues to enjoy strong growth, now representing approximately $90B of annual revenue globally. In fiscal year 2025, to support future growth we expanded our manufacturing production capabilities in meat and coffee and introduced a wide range of new Kirkland Signature items, including food-storage bags, grass-fed meat sticks, and ready-to-drink cocktails., Our digital growth globally outpaced overall sales growth in 2025, and members who engage with us through our digital channels are also more loyal. We operate eight e-commerce platforms around the world and digitally enabled sales, those initiated through a digital device and fulfilled through a warehouse or distribution center and Costco Travel, represented approximately $27B of net sales last year.
E-commerce channels provide us with the opportunity to offer an expanded selection in various categories, including precious metals, ticket programs, appliances, home furnishings, consumer electronics, lawn and garden products, health and beauty aids, apparel, and groceries. As we continue our investments in technology, we are building a multi-year roadmap to create a more seamless digital experience for members. In 2025, we delivered numerous enhancements to the member experience, both in the warehouse and online, including improvements to the Costco app, increas